In [66]:
import altair as alt
import pandas as pd

In [67]:
df = pd.read_csv('pleiades.csv')

In [68]:
df = df[df['minDate'] >= -2000]

In [69]:
featureType_gr = df.groupby(['featureTypes'])
sorted_gr = featureType_gr.size().reset_index(name='counts').sort_values('counts', ascending=False).head(10)

In [70]:
unique = sorted_gr['featureTypes'].to_numpy()

In [71]:
# we remove settlements due to their overwhelming supremacy
df = df[(df['featureTypes'].isin(unique)) & (~df['featureTypes'].str.contains("unknown")) & (~df['featureTypes'].str.contains("unlocated")) & (~df['featureTypes'].str.contains("settlement"))]

In [72]:
alt.data_transformers.disable_max_rows()
# selection a square of the heatmap
selection = alt.selection(type='single', encodings=['x', 'y'], empty='none')

heatmap = alt.Chart(df).mark_rect().encode(
    alt.X('minDate:O', axis=alt.Axis(labelAngle=0), bin=alt.Bin(step=500)),
    alt.Y('featureTypes:N'),
    # color is based on selection / this works only is one encoding (x | y) is specified in the selection above
    color=alt.condition(
        selection, alt.value('darkred'), alt.Color('count():Q', legend = alt.Legend(title = 'Legend')), 
    ),
    tooltip=["count():Q"]
).properties(
    width=350,
    height=350
).add_selection(selection)

tick = alt.Chart(df).mark_tick(height=30).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], grid=False, labels=False),
        scale=alt.Scale(),
    ),
    y=alt.Y('minDate:Q'),
    tooltip=["description:N"]
).properties(
    width=320,
    height=320,
).transform_calculate(
    # a lot of ticks have the same position due to the nature of the data set, hence we have to apply bias to create a slight shift
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).transform_filter(
    selection
).interactive()

chart = (heatmap | tick).properties(title='Emergence of pleiades from different categories over the last 4000 years (excl. settlements)')

In [73]:
chart

alt.HConcatChart(...)